<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Chaotic-Properties" data-toc-modified-id="Chaotic-Properties-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Chaotic Properties</a></span></li><li><span><a href="#Utility-Functions" data-toc-modified-id="Utility-Functions-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Utility Functions</a></span></li><li><span><a href="#Get-Features-of-Ten-Fingerprints" data-toc-modified-id="Get-Features-of-Ten-Fingerprints-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Get Features of Ten Fingerprints</a></span></li><li><span><a href="#Tests" data-toc-modified-id="Tests-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Tests</a></span></li></ul></div>

In [1]:
import os
from tensorflow.keras.applications.resnet import ResNet152, preprocess_input
from tensorflow.keras.models import Model
import numpy as np
import cv2
from sklearn.preprocessing import MinMaxScaler
import tensorflow as tf
from PIL import Image
import time
from skimage.metrics import peak_signal_noise_ratio as psnr, structural_similarity as ssim
import pickle
from bitarray import bitarray
from functools import reduce
from operator import mul, concat
from collections import Counter, OrderedDict
from nistrng import pack_sequence, unpack_sequence
from utils import generate_prns, sequence, new_map, new_map_arr

In [15]:
from nistrng import *

for i in range(10):
    key = np.random.rand(8)
    prns = generate_prns(key, 100000)
    prns = (prns * (2**32)).astype(np.uint32).view(np.uint8)
    prns = pack_sequence(prns)
#     prns = "".join(prns.astype(str))
#     with open(f"check-for-randomness/{i+1}.txt", "w") as f:
#         f.write(prns)
    results, exp = run_by_name_battery("maurers_universal", prns, SP800_22R1A_BATTERY)
    print(results.score)

0.9949496015729947
0.9972524846634215
0.9968918862234086
0.9969391636882995
0.9959295346061479
0.9958588205870846
0.9954174359785051
0.9958835795278886
0.9955241306315238
0.9971434607851433


# Chaotic Properties

In [26]:
import pandas as pd
import seaborn as sns
from matplotlib import cm
from matplotlib.colors import ListedColormap

nist_table = pd.read_csv("nistrng.csv")
nist_table = nist_table.set_index("Test")

fig = plt.figure(figsize=(40, 20), dpi=600)
cmap = cm.get_cmap("YlGnBu", 12)
mat = np.array(cmap(np.linspace(0, 1, 10000)))
mat[:75] = np.array([1, 0.43, 0.43, 1])
cmap = ListedColormap(mat)

plt.rcParams.update({"font.size": 18})
ax = sns.heatmap(nist_table.T, cmap=cmap, annot=True, fmt='.4f', annot_kws={"fontsize": 18})
plt.show()

In [ ]:
fig = plt.figure(figsize=(50, 50))
ax1 = fig.add_subplot(111, projection='3d')
# ax2 = fig.add_subplot(122, projection='3d')

n = 2000
a = np.linspace(0, 1, n)
b = np.linspace(0, 1, n)
x = 0.1 * np.ones(n)
y = 0.1 * np.ones(n)
x1 = 0.1 * np.ones(n)
y1 = 0.1 * np.ones(n)

ax1.xaxis.set_tick_params(labelsize=36)
ax1.yaxis.set_tick_params(labelsize=36)
ax1.zaxis.set_tick_params(labelsize=36)

for j in range(2000):
    x, y = new_map_arr(x, y, a, np.ones(a.size) * 0.564)
    x1, y1 = new_map_arr(x1, y1, np.ones(a.size) * 0.115, b)
    if j > 2000-100:
        ax1.scatter(a, x, zs=0, zdir='y', marker=',', color='red', alpha=0.5)
        ax1.scatter(a, y, zs=0.33, zdir='y', marker=',', color='purple', alpha=0.5)
        ax1.scatter(b, x1, zs=0.66, zdir='y', marker=',', color='green', alpha=0.5)
        ax1.scatter(b, y1, zs=1, zdir='y', marker=',', color='blue', alpha=0.5)
plt.legend(["X vs A", "Y vs A", "X vs B", "Y vs B"], fontsize=28, markerscale=5)
plt.show()

In [ ]:
def calc_lyapunov(arr):
    abs_arr = np.abs(np.diff(arr))
    return np.mean(np.log(abs_arr[abs_arr != 0]))

larr = []
for i in np.linspace(0, 1, 100):
    for j in np.linspace(0, 1, 100):
        arr = [*np.random.rand(2)]
        for j in range(1000):
            arr.extend(new_map(arr[-1], arr[-2], a=i, b=j))
        arr = np.abs(arr / np.max(arr))
        larr.append((calc_lyapunov(arr[::2] * (2 ** 32)), calc_lyapunov(arr[1::2] * (2 ** 32))))
    
larr = np.array(larr)

print("Min:", np.min(larr[:, 0]), np.min(larr[:, 1]))
print("Max:", np.max(larr[:, 0]), np.max(larr[:, 1]))
print("Mean:", np.mean(larr[:, 0]), np.mean(larr[:, 1]))

X, Y = np.meshgrid(np.linspace(0, 1, 100), np.linspace(0, 1, 100))
Z = larr[:, 0].reshape(100, 100)
Z2 = larr[:, 1].reshape(100, 100)

fig = plt.figure(figsize=(30, 30))
ax1= fig.add_subplot(121, projection='3d')
ax2 = fig.add_subplot(122, projection='3d')

ax1.set_zlim(20.2, 21)
ax1.set_xlabel("K1")
ax1.set_ylabel("K2")
ax1.plot_surface(X, Y, Z, cmap='YlGnBu')

ax2.set_zlim(20.2, 21)
ax2.set_xlabel("K1")
ax2.set_ylabel("K2")
ax2.plot_surface(X, Y, Z2, cmap='YlGnBu')

plt.subplots_adjust(hspace=0.01, wspace=0.01)

# Utility Functions

In [2]:
def nC(data, ret):
    data = data.flatten()
    ret = ret.flatten()
    
    obs1 = np.sqrt(np.sum(np.power(data, 2)))
    obs2 = np.sqrt(np.sum(np.power(ret, 2)))
    obs3 = np.sum(data * ret)
    
    return obs3 / (obs1 * obs2)

def biterr(data, ret):
    data = data.flatten()
    ret = ret.flatten()
    
    total_bits = data.size * data.itemsize * 8
    bits = np.bitwise_xor(data, ret)
    count = 0
    for i in bits:
        count += format(i, "08b").count('1')
    return count / total_bits

In [3]:
model = ResNet152()
model = Model(inputs = model.inputs, outputs = model.layers[-2].output)

In [4]:
img = cv2.imread('dataset/1__M_Left_index_finger.BMP')
img = cv2.resize(img,(224,224))     # resize image to match model's expected sizing
img = np.reshape(img,[1,224,224,3]) # return the image with shaping that TF wants.
feature = model.predict(img, verbose=0)[0]
scl = (tf.math.sigmoid(feature).numpy() * (2**32)).astype(np.uint32)

In [5]:
feature.shape

(2048,)

In [6]:
KEY = 0x905068f65172c3606e2b2b3fdda0b9de3d3cd130e90ee1e6927da9c4ffcffede
p = []
for i in range(8):
    p.append((KEY >> (32 * i)) & 0xffffffff)
p = np.array(p)

feature = scl.reshape((-1, 8))
for i in range(len(feature)):
    feature[i] = feature[i] ^ p
feature = feature.flatten()

In [7]:
def get_initial(vec):
    p = []
    for i in range(8):
        p.append(np.bitwise_xor.reduce(vec[i::8]))
    return p

def prns(vec, size, data=None):
    rs = []
    for i in range(len(vec)):
        np.random.seed(vec[i])
        a1 = np.random.randint(0, 256, size, dtype=np.uint8)
        rs.append(a1)
    rs = np.array(rs)
    seq = np.zeros(rs[0].size, dtype=np.uint8)
    for i in range(len(rs)):
        seq = seq ^ rs[i]
    return seq

def substitute(img, r):
    c = img.copy()
    shape = img.shape
    c = c.flatten()
    args = np.argsort(r)
    
    for i in range(c.size):
        c[i], c[args[i]] = c[i] ^ c[args[i]], c[i]
    return c.reshape(shape)

def desubstitute(img, r):
    c = img.copy()
    shape = img.shape
    c = c.flatten()
    args = np.argsort(r)
    
    for i in range(c.size-1, -1, -1):
        c[i], c[args[i]] = c[args[i]], c[i] ^ c[args[i]]
    return c.reshape(shape)


def diffusion(img, r):
    c = img.copy()
    shape = img.shape
    r = r.reshape(shape)
    
    for _ in range(2):
        for i in range(shape[0]):
            c[i] = ((c[i] ^ c[i-1]) + r[i]) % 256
        for j in range(shape[1]):
            c[:, j] = ((c[:, j] ^ c[:, j-1]) + r[:, j]) % 256
        
    return c

def dediffusion(img, r):
    c = img.copy()
    shape = img.shape
    r = r.reshape(shape)
    
    for _ in range(2):
        for j in range(shape[1]-1, -1, -1):
            c[:, j] = ((c[:, j] - r[:, j]) % 256) ^ c[:, j-1] 
        for i in range(shape[0]-1, -1, -1):
            c[i] = ((c[i] - r[i]) % 256) ^ c[i-1]
        
    return c

def DoEnc(img, vec, data=None):
    rs = prns(vec, img.size)
    c = img.copy()
    c = substitute(c, rs)
    c = diffusion(c, rs)
    c = substitute(c, rs)
    c = diffusion(c, rs)
    return c

def DoDec(img, vec, data=None):
    rs = prns(vec, img.size, data=None)
    c = img.copy()
    c = dediffusion(c, rs)
    c = desubstitute(c, rs)
    c = dediffusion(c, rs)
    c = desubstitute(c, rs)
    return c

def embed_data(img, data, seed=10):
    img = img.copy()
    shape = img.shape
    img = img.flatten()
    np.random.seed(seed)
    r = np.random.randint(0, 256, img.size)
    indices = np.argsort(r)
    
    for i in range(len(data)):
        bit = r[i] % 3
        new = (img[indices[i]] & 0b11111000) + (data[i] << bit)
        if bit == 0:
            new += (img[indices[i]] & 0b110) # 6
        elif bit == 1:
            new += (img[indices[i]] & 0b101) # 5
        else:
            new += (img[indices[i]] & 0b011) # 3
        img[indices[i]] = new
    
    return img.reshape(shape)

def extract_data(img, data_len, seed=10):
    img = img.flatten()
    np.random.seed(seed)
    r = np.random.randint(0, 256, img.size)
    indices = np.argsort(r)
    data = np.zeros(data_len, dtype=np.uint8)
    
    for i in range(data_len):
        bit = r[i] % 3
        if bit == 0:
            data[i] = (img[indices[i]] & 0b001)
        elif bit == 1:
            data[i] = (img[indices[i]] & 0b010) >> 1
        else:
            data[i] = (img[indices[i]] & 0b100) >> 2
    
    return data

In [8]:
vec = get_initial(feature)
img = np.array(Image.open("cover/lena.png").convert("RGB"))
data = np.random.randint(0, 2, img.size)
org = img.copy()

start = time.perf_counter()
img = embed_data(img, data)
print("Embedding Time:", time.perf_counter() - start)
print("PSNR after embedding:", psnr(org, img))
print("SSIM after embedding:", ssim(org, img, channel_axis=2), end='\n\n')

start = time.perf_counter()
enc = DoEnc(img, vec)
print("Encryption Time:", time.perf_counter() - start)

start = time.perf_counter()
dec = DoDec(enc, vec)
print("Decryption Time:", time.perf_counter() - start)

start = time.perf_counter()
ret = extract_data(dec, len(data))

print("Extraction Time: ", time.perf_counter() - start)
print("nC:", nC(data, ret))
print("BER:", biterr(data, ret))

fig, ax = plt.subplots(1, 6, figsize=(60, 10))
ax[0].imshow(org)
ax[1].imshow(data.reshape(org.shape) * 255)
ax[2].imshow(img)
ax[3].imshow(enc)
ax[4].imshow(dec)
ax[5].imshow(ret.reshape(org.shape) * 255)

FileNotFoundError: [Errno 2] No such file or directory: 'cover/lena.png'

In [14]:
class NodeTree(object):
    def __init__(self, left=None, right=None):
        self.left = left
        self.right = right

    def children(self):
        return (self.left, self.right)

    def nodes(self):
        return (self.left, self.right)

    def __str__(self):
        return '%s_%s' % (self.left, self.right)

class CustomHuffmanCoding():
    def __generate_sequence(self, vec, length, k=2**32):
#         np.random.seed(vec[0])
        vec = np.array(vec).astype(np.float64) / k
        a1 = generate_prns(vec, length // 4)
#         a1 = np.random.rand(length//4)
        seq = (a1 * k).astype(np.uint32).view(np.uint8)
        return seq[:length]
    
    def __prediction_map_generation(self, image: np.array, confuse=True, mp=None) -> np.array:
        image = image.astype(np.int16)
        p = np.zeros(image.shape, dtype=np.int16)
        if len(image.shape) == 3:
            w, h, d = image.shape
            for k in range(d):
                for i in range(w):
                    for j in range(h):
                        if i == 0 and j == 0:
                            p[i, j, k] = image[i, j, k]
                        elif i == 0 and j > 0:
                            p[i, j, k] = image[i, j, k] - image[i, j-1, k]
                        elif i > 0 and j == 0:
                            p[i, j, k] = image[i, j, k] - image[i-1, j, k]
                        else:
                            a = int(image[i-1, j-1, k])
                            b = int(image[i, j-1, k])
                            c = int(image[i-1, j, k])
                            if a >= max(b, c):
                                p[i, j, k] = image[i, j, k] - min(b, c)
                            elif a <= min(b, c):
                                p[i, j, k] = image[i, j, k] - max(b, c)
                            else:
                                p[i, j, k] = image[i, j, k] - (b+c-a)
        else:
            w, h = image.shape
            for i in range(w):
                for j in range(h):
                    if i == 0 and j == 0:
                        p[i, j] = image[i, j]
                    elif i == 0 and j > 0:
                        p[i, j] = image[i, j] - image[i, j-1]
                    elif i > 0 and j == 0:
                        p[i, j] = image[i, j] - image[i-1, j]
                    else:
                        a = int(image[i-1, j-1])
                        b = int(image[i, j-1])
                        c = int(image[i-1, j])
                        if a >= max(b, c):
                            p[i, j] = image[i, j] - min(b, c)
                        elif a <= min(b, c):
                            p[i, j] = image[i, j] - max(b, c)
                        else:
                            p[i, j] = image[i, j] - (b+c-a)
        if confuse:
            args = np.argsort(mp[:p.size])
            p = p.flatten()[args].reshape(p.shape)
        return p

    def __inverse_prediction_map(self, p: np.array, confuse=True, mp=None) -> np.array:
        if confuse:
            args = np.argsort(mp[:p.size])
            args = np.argsort(args)
            p = p.flatten()[args].reshape(p.shape)

        img = np.zeros(p.shape, dtype=np.uint8)
        if len(p.shape) == 3:
            w, h, d = img.shape
            for k in range(d):
                for i in range(w):
                    for j in range(h):
                        if i == 0 and j == 0:
                            img[i, j, k] = p[i, j, k]
                        elif i == 0 and j > 0:
                            img[i, j, k] = p[i, j, k] + img[i, j-1, k]
                        elif i > 0 and j == 0:
                            img[i, j, k] = p[i, j, k] + img[i-1, j, k]
                        else:
                            a = int(img[i-1, j-1, k])
                            b = int(img[i, j-1, k])
                            c = int(img[i-1, j, k])
                            if a >= max(b, c):
                                img[i, j, k] = p[i, j, k] + min(b, c)
                            elif a <= min(b, c):
                                img[i, j, k] = p[i, j, k] + max(b, c)
                            else:
                                img[i, j, k] = p[i, j, k] + (b+c-a)
        else:
            w, h = img.shape
            for i in range(w):
                for j in range(h):
                    if i == 0 and j == 0:
                        img[i, j] = p[i, j]
                    elif i == 0 and j > 0:
                        img[i, j] = p[i, j] + img[i, j-1]
                    elif i > 0 and j == 0:
                        img[i, j] = p[i, j] + img[i-1, j]
                    else:
                        a = int(img[i-1, j-1])
                        b = int(img[i, j-1])
                        c = int(img[i-1, j])
                        if a > max(b, c):
                            img[i, j] = p[i, j] + min(b, c)
                        elif a < min(b, c):
                            img[i, j] = p[i, j] + max(b, c)
                        else:
                            img[i, j] = p[i, j] + (b+c-a)
        return (img % 256).astype(np.uint8)
    
    def __generate_initial_hct(self, p):
        counter = Counter(p.flatten())
        codes = self.__generate_codes(counter, dtype=np.int16)
        L = dict(map(lambda x: (x[0], len(x[1])), codes.items()))
        V = OrderedDict()
        for i, (k, v) in enumerate(L.items()):
            V[v] = V.get(v, []) + [i]
        return codes, L, V


    def __generate_tvhct(self, codes, v, l: dict, timeFrame=time.time()):
        t = round(timeFrame)
        np.random.seed(t)
        for i in v:
            np.random.shuffle(v[i])
        v = list(map(lambda x: x[1], v.items()))
        v = reduce(concat, v)
        newL = []
        keys = list(l.keys())
        for i in v:
            newL.append((keys[i], codes[keys[v[i]]]))

        newDict = OrderedDict()
        newL = dict(newL)

        for i in codes.keys():
            newDict[i] = newL[i]
        return newDict

    def __huffman_code_tree(self, node, dtype=str, left=True, binString=''):
        if type(node) is dtype:
            return {node: binString}
        (l, r) = node.children()
        d = dict()
        d.update(self.__huffman_code_tree(l, dtype=dtype, left=True, binString=binString + '0'))
        d.update(self.__huffman_code_tree(r, dtype=dtype, left=False, binString=binString + '1'))
        return d


    def __generate_codes(self, counter, dtype=str):
        freq = sorted(counter.items(), key=lambda x: x[1], reverse=True)
        nodes = freq

        while len(nodes) > 1:
            (key1, c1) = nodes[-1]
            (key2, c2) = nodes[-2]
            nodes = nodes[:-2]
            node = NodeTree(key1, key2)
            nodes.append((node, c1 + c2))

            nodes = sorted(nodes, key=lambda x: x[1], reverse=True)

        huffmanCode = self.__huffman_code_tree(nodes[0][0], dtype=dtype)
        return dict(sorted(huffmanCode.items(), key=lambda x: len(x[1])))
    
    def encode(self, p, key):
        seq = self.__generate_sequence(key, reduce(mul, self.shape))
        p = self.__prediction_map_generation(p, confuse=True, mp=seq)
        
        self.codes = []
        self.codes_inv = []
        self.lengths = []
        self.length_of_codes = [[], [], []]
        
        full = ""
        for channel in range(3):
            codes_r, L_r, V_r = self.__generate_initial_hct(p[:, :, channel])
            self.codes.append(self.__generate_tvhct(codes_r, V_r, L_r, timeFrame=self.timeFrame))
            self.codes_inv.append(dict(zip(self.codes[channel].values(), self.codes[channel].keys())))

            string = ""
            a = p[:, :, channel].flatten()
            for i in range(len(a)):
                string += self.codes[channel][a[i]]
                self.length_of_codes[channel].append(len(self.codes[channel][a[i]]))
            full += string
            self.lengths.append(len(string))
        
        data = np.array(bitarray(full).tolist())
        data = unpack_sequence(data).astype(np.uint8)
        ra = seq.astype(np.uint8)
        for _ in range(2):
            for i in range(len(data)):
                data[i] = (data[i] + data[i-1] + ra[i]) % 256
    
        return data
    
    def decode(self, data, key):
        seq = self.__generate_sequence(key, reduce(mul, self.shape))
        
        data = np.array(data)
        ra = seq.astype(np.uint8)
        for _ in range(2):
            for i in range(len(data)-1, -1, -1):
                data[i] = (data[i] - data[i-1] - ra[i]) % 256
    
        n = bitarray()
        n.extend(pack_sequence(data))
        data = n
        full_data = data.to01()
        ret = np.zeros(self.shape)
        for channel in range(3):
            start = 0 if channel == 0 else sum(self.lengths[:channel])
            data = full_data[start: start + self.lengths[channel]]
            i = 0
            count = 0
            pixels = []
            while i < len(data):
                j = i + self.length_of_codes[channel][count]
                if data[i: j] in self.codes_inv[channel]:
                    pixels.append(self.codes_inv[channel][data[i: j]])
                i = j
                count += 1
            pixels = np.array(pixels)[:reduce(mul, self.shape[:2])].reshape(self.shape[:2])
            ret[:, :, channel] = pixels
        ret = self.__inverse_prediction_map(ret, confuse=True, mp=seq)
        return ret
    
    def get_codes_from_file(f):
        self.codes = pickle.load(f)
        self.codes_inv = dict(zip(self.codes.values(), self.codes.keys()))
        
    def save_codes_to_file(f):
        pickle.dump(self.codes, f)
    
    def __init__(self, shape, timeFrame=None):
        self.shape = shape
        self.timeFrame = timeFrame if timeFrame else time.time()

In [19]:
vec = get_initial(feature)
img = np.array(Image.open("cover/volume-0_slice_0.jpg").resize((512, 512)).convert("RGB"))
data = np.random.randint(0, 2, img.size)
org = img.copy()

start = time.perf_counter()
img = embed_data(img, data)
print("Embedding Time:", time.perf_counter() - start)
print("PSNR after embedding:", psnr(org, img))
print("SSIM after embedding:", ssim(org, img, channel_axis=2), end='\n\n')

start = time.perf_counter()
encoder = CustomHuffmanCoding(shape=img.shape)
enc = encoder.encode(img, vec)
print("Encryption Time:", time.perf_counter() - start)

start = time.perf_counter()
dec = encoder.decode(enc, vec)
print("Decryption Time:", time.perf_counter() - start)

vec2 = vec.copy()
vec2[0] += 1
dec2 = encoder.decode(enc, vec2)

start = time.perf_counter()
ret = extract_data(dec, len(data))

print("Extraction Time: ", time.perf_counter() - start)
print("nC:", nC(data, ret))
print("BER:", biterr(data, ret))
print("CR:", len(enc) / (img.size))

fig, ax = plt.subplots(1, 3, figsize=(30, 10))
ax[0].imshow(img)
ax[1].imshow(dec)
ax[2].imshow(dec2)

Embedding Time: 3.4156171999999856
PSNR after embedding: 42.696770836323935
SSIM after embedding: 0.911483230882108



C:\Users\ADMIN\AppData\Local\Temp/ipykernel_7016/1412423077.py:206: RuntimeWarning: overflow encountered in ubyte_scalars
  data[i] = (data[i] + data[i-1] + ra[i]) % 256


Encryption Time: 6.174829500000044


C:\Users\ADMIN\AppData\Local\Temp/ipykernel_7016/1412423077.py:217: RuntimeWarning: overflow encountered in ubyte_scalars
  data[i] = (data[i] - data[i-1] - ra[i]) % 256


Decryption Time: 4.551827399999979


ValueError: cannot reshape array of size 59703 into shape (512,512)

# Get Features of Ten Fingerprints

In [ ]:
fingerprints = []
files = os.listdir("./dataset")
for file in files:
    picPath = os.path.join("dataset", file)
    img = np.array(Image.open(picPath).convert("RGB").resize((224, 224)))
    fingerprints.append(img)
fingerprints = np.array(fingerprints)

data = model.predict(fingerprints, verbose=0)[:1].flatten()
data = pack_sequence(np.round(data * (2**32)).astype(np.uint32).view(np.uint8))

In [ ]:
print(data.shape)

# Tests

In [ ]:
from tqdm.notebook import tqdm
from scipy.stats import pearsonr
import pandas as pd
import logging

def runTests(path, data):
    try:
        files = os.listdir(path)
        results = []
        for picName in tqdm(files, desc="Tests"):
            try:
                picPath = os.path.join(path, picName)
                img = np.array(Image.open(picPath).convert("RGB"))
                org = img.copy()
                img = embed_data(img, data)
                img2 = img.copy()
                img2[np.random.randint(0, min(img2.shape), 2)] ^= 1
                encoder = CustomHuffmanCoding(shape=img.shape)
                encoder2 = CustomHuffmanCoding(shape=img.shape)
                start = time.perf_counter()
                enc = encoder.encode(img, vec)
                enc_time = time.perf_counter() - start
                enc2 = encoder2.encode(img2, vec)

                start = time.perf_counter()
                dec = encoder.decode(enc, vec)
                dec_time = time.perf_counter() - start

                ext = extract_data(dec, len(data))
                n, _ = np.histogram(org.flatten(), bins=256)
                n = n[n > 0] / org.size
                entropy_plain = np.sum(-n * np.log2(n))

                n, _ = np.histogram(enc, bins=256)
                n = n / enc.size
                entropy = np.sum(-n * np.log2(n))
                
                seed = np.random.randint(0, 256, org.size-1)
                seed = np.argsort(seed)
                corr_plain = pearsonr(org.flatten()[seed[:5000]], org.flatten()[seed[:5000]+1])[0]
                correlation = pearsonr(enc, np.roll(enc, 1))[0]
                cr = len(enc) / (img.size)
                length = min(enc.size, enc2.size)
                npcr = enc[enc2[:length] != enc[:length]].size / length
                uaci = np.sum(np.abs(enc2[:length].astype(np.int32) - enc[:length].astype(np.int32)) / 256) / length
                nc = nC(data, ext)
                ber = biterr(data, ext)

                print(f"{picName=}\n{psnr(org, img)=}\n{ssim(org, img, channel_axis=2)=}\n{npcr=}\n{uaci=}\n{entropy_plain=}\n{entropy=}\n{corr_plain=}\n{correlation=}\n{cr=}\n{nc=}\n{ber=}\n{enc_time=}\n{dec_time=}")
                fig, ax = plt.subplots(1, 3, figsize=(40, 10))
                ax[0].imshow(org)
                ax[1].hist(org.flatten(), bins=256)
                ax[2].bar(np.arange(0, 256), n*enc.size)
                plt.show()

                indices = np.random.randint(0, org.size-1, 5000)
                fig, ax = plt.subplots(1, 3, figsize=(30, 10))
                ax[0].imshow(org)
                ax[1].scatter(org.flatten()[indices], np.roll(org.flatten()[indices+1], 1))
                indices = np.random.randint(0, enc.size-1, 5000)
                ax[2].scatter(enc.flatten()[indices], np.roll(enc.flatten()[indices+1], 1))
                plt.show()

                results.append((picName, "x".join(np.array(org.shape, dtype=str)), psnr(org, img), ssim(org, img, channel_axis=2), npcr, uaci, entropy_plain, entropy, corr_plain, correlation, cr, nc, ber, enc_time, dec_time))
            except Exception as e:
                logging.exception(e)
    except KeyboardInterrupt as e:
        pass
    finally:
        results = pd.DataFrame(results, columns=["Image", "Size", "PSNR", "SSIM", "NPCR", "UACI", "Entropy Plain", "Entropy", "Correlation Plain", "Correlation", "CR", "NC", "BER", "Enc time", "Dec time"])
        results.to_csv(f"results-{path}.csv", index=False)
        return results

In [ ]:
runTests("sea-animals-dataset", data)

In [ ]:
runTests("spleen", data)